In [74]:
%pip install numpy
%pip install pymoo
%pip install deap
%pip install matplotlib
%pip install plotly
%pip install nbformat

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [75]:
import numpy as np
from textwrap import wrap
from deap import benchmarks
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from pymoo.algorithms.soo.nonconvex.ga import GA
from pymoo.algorithms.moo.nsga2 import NSGA2
from pymoo.optimize import minimize
from pymoo.core.problem import Problem

# _Genetic Algorithms_ <span style="margin-left: 10px; font-size: .6em;">an introduction</span>

For any question just drop me an email at luca.zanussi01@universitadipavia.it

### Define the problem

Here's a simple one, we want to minimize the following function in 6 variables (i.e., genes, in terms of the GA):

$$f(\mathbf{x}) := \left| \sum_{i=1}^6{x_i} - 42 \right| \qquad x_i \in [0, 20]$$

This translates in practice to the search for individuals in which genes, when summed, lead up to 42.
We also want to apply this constraint to the variables of the problem:

$$x_3^2 - x_1 + 2 = 0$$

In [76]:
fn = lambda X: abs(sum(X) - 42)
co = lambda X: X[2]**2 - X[0] + 2

class MyProblem(Problem):
    def _evaluate(self, design, out, *args, **kwargs):
        out['F'] = np.array([ fn(X) for X in design ])
        out['G'] = np.array([ co(X) for X in design ])

problem = MyProblem(n_var=6, n_obj=1, n_ieq_constr=1, xl=[0]*6, xu=[20]*6)

### Run the Genetic Algorithm

Pymoo wants a _problem_, an _algorithm_ and a _stopping criteria_.
Here we want to use the simple, basic GA with a population size of 100 and we stop it at its 100<sup>th</sup> generation.

In [77]:
algorithm = GA(pop_size=100)
stop_criteria = ('n_gen', 100)

res = minimize(problem, algorithm, stop_criteria, seed=5, verbose=True)

n_gen  |  n_eval  |     cv_min    |     cv_avg    |     f_avg     |     f_min    
     1 |      100 |  0.000000E+00 |  1.329865E+02 |  1.466899E+01 |  1.9787114153
     2 |      200 |  0.000000E+00 |  1.478461E+01 |  1.157774E+01 |  1.4449677418
     3 |      300 |  0.000000E+00 |  0.8153545008 |  1.196700E+01 |  0.1571098946
     4 |      400 |  0.000000E+00 |  0.000000E+00 |  4.5476723796 |  0.0056722606
     5 |      500 |  0.000000E+00 |  0.000000E+00 |  2.0835592324 |  0.0056722606
     6 |      600 |  0.000000E+00 |  0.000000E+00 |  1.0922047662 |  0.0056722606
     7 |      700 |  0.000000E+00 |  0.000000E+00 |  0.6643455313 |  0.0015934932
     8 |      800 |  0.000000E+00 |  0.000000E+00 |  0.4596743872 |  0.0015934932
     9 |      900 |  0.000000E+00 |  0.000000E+00 |  0.3302723719 |  0.0015934932
    10 |     1000 |  0.000000E+00 |  0.000000E+00 |  0.2623796129 |  0.0015934932
    11 |     1100 |  0.000000E+00 |  0.000000E+00 |  0.2096305198 |  0.0015934932
    12 |     120

> The [documentation of pymoo](https://pymoo.org/index.html) is quite good, you might want to check it out!
>
> Also, you can give a look at the code... see the [constructor of the GA class](https://github.com/anyoptimization/pymoo/blob/2ca840e30f49bb26c8ea796490eb7d345d557703/pymoo/algorithms/soo/nonconvex/ga.py#L58)? It takes a lot of different parameters among which the implementations of _crossover_, _mutation_ and _selection_, which can be changed.

#### Analyze the result

Here you can see the value of the genes, as well the minimized objective.

In [78]:
print('Genes:     ', res.X)
print('Objective: ', res.F)

Genes:      [14.878155    2.6758207   1.56603646  5.02281141  1.70162772 16.15554871]
Objective:  [8.86089424e-10]


In fact, the sum of the genes is 42...

In [79]:
sum(res.X)

41.99999999911391

...and the constraint is not violated.

In [80]:
res.X[2] ** 2 - res.X[0] + 2

-10.425684794271302

## _Bonus_: an alternative problem

There are lots of well-known benchmark optimization problems online,
see [Wikipedia](https://en.wikipedia.org/wiki/Test_functions_for_optimization) or the [Pymoo documentation](https://pymoo.org/problems/test_problems.html).

For example, let's see the **Ackley function**, it has a lot of global minima and it takes two variables in the range $[-32, 32]$.

In [81]:
X = np.arange(-32, 32, .5)
Y = np.arange(-32, 32, .5)
X, Y = np.meshgrid(X, Y)
Z = np.empty(X.shape)

for i in range(X.shape[0]):
    for j in range(X.shape[1]):
        Z[i, j] = benchmarks.ackley((X[i, j], Y[i, j]))[0]

fig = go.Figure(data=[go.Surface(z=Z, x=X, y=Y)])
fig.update_layout(title='Ackley', autosize=False,
                  width=800, height=500,
                  margin=dict(l=65, r=50, b=65, t=90))
fig.show()

And define a problem for it, then run the GA.

In [82]:
class AckleyProblem(Problem):
    def __init__(self, **kwargs):
        super().__init__(n_var=2, n_obj=1, xl=[-32]*2, xu=[32]*2, **kwargs)

    def _evaluate(self, design, out, *args, **kwargs):
        out['F'] = np.array([benchmarks.ackley(d) for d in design])

problem = AckleyProblem()
algorithm = GA(pop_size=100)
stop_criteria = ('n_gen', 100)

res = minimize(problem, algorithm, stop_criteria, seed=5, verbose=True)

n_gen  |  n_eval  |     f_avg     |     f_min    
     1 |      100 |  2.000794E+01 |  9.5682581118
     2 |      200 |  1.763051E+01 |  7.7737054274
     3 |      300 |  1.447547E+01 |  3.3753063077
     4 |      400 |  1.127316E+01 |  3.3753063077
     5 |      500 |  8.9976443103 |  3.3389865195
     6 |      600 |  7.1616208594 |  2.4434815408
     7 |      700 |  5.9406739539 |  1.7331978646
     8 |      800 |  4.9648205291 |  0.7958824838
     9 |      900 |  4.3629890183 |  0.7958824838
    10 |     1000 |  3.6999117819 |  0.7958824838
    11 |     1100 |  3.2272596478 |  0.3719264808
    12 |     1200 |  2.8268404873 |  0.3719264808
    13 |     1300 |  2.5135162265 |  0.3719264808
    14 |     1400 |  2.0957622271 |  0.3719264808
    15 |     1500 |  1.8230680670 |  0.3719264808
    16 |     1600 |  1.5306996018 |  0.2556466529
    17 |     1700 |  1.2229065059 |  0.1740952289
    18 |     1800 |  0.9870318684 |  0.1740952289
    19 |     1900 |  0.8295046372 |  0.1740952289


The GA should have correctly found the global minimum at $\mathbf{x} = (0, 0)$.

In [83]:
print('Genes:     ', res.X)
print('Objective: ', res.F)

Genes:      [-5.37039672e-05 -3.21451803e-04]
Objective:  [0.00092463]


## Multi-Objective optimization

Here we want to minimize the Kursawe functions, we use NSGA-II since this is a multi-objective problem.

In [84]:
X = np.arange(-5, 5, .1)
Y = np.arange(-5, 5, .1)
X, Y = np.meshgrid(X, Y)

Z1 = np.empty(X.shape)
Z2 = np.empty(X.shape)

for i in range(X.shape[0]):
    for j in range(X.shape[1]):
        Z1[i, j], Z2[i, j] = benchmarks.kursawe((X[i, j], Y[i, j]))

In [85]:
fig = make_subplots(rows=1, cols=2,
                    specs=[[{'is_3d': True}, {'is_3d': True}]],
                    subplot_titles=['Kursawe <i>f<sub>1</sub></i>', 'Kursawe <i>f<sub>2</sub></i>'])
fig.add_trace(go.Surface(x=X, y=Y, z=Z1, colorbar_x=-0.15), 1, 1)
fig.add_trace(go.Surface(x=X, y=Y, z=Z2), 1, 2)
fig.update_layout(height=600)
fig.show()

Let's define the problem for Pymoo and run NSGA-II

In [86]:
class KursaweProblem(Problem):
    def __init__(self, **kwargs):
        super().__init__(n_var=2, n_obj=2, xl=[-5, -5], xu=[5, 5], **kwargs)

    def _evaluate(self, design, out, *args, **kwargs):
        out['F'] = np.array([benchmarks.kursawe(d) for d in design])

problem = KursaweProblem()
algorithm = NSGA2(pop_size=100)
stop_criteria = ('n_gen', 100)

res = minimize(problem, algorithm, stop_criteria, seed=5, verbose=True)

n_gen  |  n_eval  | n_nds  |      eps      |   indicator  
     1 |      100 |      6 |             - |             -
     2 |      200 |     10 |  0.0770833958 |             f
     3 |      300 |     16 |  0.1689934646 |         ideal
     4 |      400 |     17 |  0.0367893889 |         ideal
     5 |      500 |     20 |  0.2570025789 |         ideal
     6 |      600 |     26 |  0.0119782199 |             f
     7 |      700 |     32 |  0.0263963472 |         ideal
     8 |      800 |     40 |  0.0242526041 |         ideal
     9 |      900 |     51 |  0.0374202343 |         ideal
    10 |     1000 |     66 |  0.0037032299 |             f
    11 |     1100 |     76 |  0.0024908004 |             f
    12 |     1200 |     87 |  0.0050681807 |         nadir
    13 |     1300 |     92 |  0.0014243518 |             f
    14 |     1400 |    100 |  0.0028095764 |             f
    15 |     1500 |    100 |  0.0009857640 |             f
    16 |     1600 |    100 |  0.0021792432 |            

Differently from the single objective problem, here we have many solutions that do not dominate each other.

If you get 100 solutions, all individuals in the last generation got their place on the Pareto front; this might not always be the case, especially if you perform fewer iterations of the GA.

In [87]:
len(res.X)

100

Let's pick a random solution and analyze it, we have 2 parameters (genes) and two objective values, one for each Kursawe function.

In [88]:
print('Genes:      ', res.X[0])
print('Objectives: ', res.F[0])

Genes:       [-0.00047409 -0.00012237]
Objectives:  [-9.99902078e+00  2.93280209e-03]


As a last thing, we draw the Pareto front formed by all the non-dominated solutions to the problem.

In [89]:
res_xy = res.F.T
res_ord = np.argsort(res_xy[0])  # This is to sort individuals by their f1 value and to be able to draw a nice line to connect them

fig = go.Figure(data=go.Scatter(x=res_xy[0,res_ord], y=res_xy[1,res_ord],
                                text=[f'<b>Genes: {"<br>".join(wrap(str(x)))}</b>' for x in res.X],
                                mode='lines+markers'))
fig.update_layout(width=800, height=600, title=f'NSGA-II solutions for {problem.name()}', xaxis_title='f1', yaxis_title='f2')
fig.show()

_That's All Folks!_